In [1]:
import keras
import datetime
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
# Setting seed for reproducability
np.random.seed(1234)  
PYTHONHASHSEED = 0
from sklearn import preprocessing
from sklearn.metrics import confusion_matrix, recall_score, precision_score
from keras import models
from keras.wrappers.scikit_learn import KerasRegressor
from keras.models import Sequential,model_from_json
from keras.layers import Dense, Dropout, LSTM, Activation
%matplotlib inline
from decimal import Decimal
import warnings
warnings.filterwarnings("ignore")
import pickle
from sklearn.preprocessing import OneHotEncoder,LabelEncoder,Normalizer, MinMaxScaler
from sklearn.cross_validation import cross_val_score
from sklearn.model_selection import GridSearchCV
from numpy.random import seed
seed(1)
from tensorflow import set_random_seed
set_random_seed(2)
from sklearn.metrics import mean_absolute_error
from sklearn import ensemble
from sklearn.ensemble import RandomForestRegressor
from sklearn.multioutput import MultiOutputRegressor
import xgboost as xgb

import pickle
from sklearn.externals import joblib
import os
import re

Using TensorFlow backend.


In [2]:
# df=pd.read_csv('C:\\Users\\lengada1\\NCSU\\ten_skus.csv')
df=pd.read_csv('~/Downloads/NCSU-master-2/ten_skus.csv')
df['Date'] = pd.to_datetime(df['Date'])
df['Year'] = df['Date'].dt.year
df['Month'] = df['Date'].dt.month
df['Day'] = df['Date'].dt.weekday_name

day_dummy=pd.get_dummies(df.Day)
df=pd.concat([df,day_dummy],axis=1)
df.drop(['Day','Date'],inplace=True,axis=1)


In [3]:
def split_df(df):
    d={}
    split_by_list=np.unique(df.id.values)
    for sku in split_by_list:
        d[sku]=df[df.id==sku]
    return d

df_dict=split_df(df);


In [4]:
y={}
for sku in list(df_dict.keys()):
    y[sku]=df_dict[sku]['Sales']

In [5]:
X={}
X_raw={}
for sku in list(df_dict.keys()):
    X_raw[sku]=df_dict[sku]
    X_raw[sku]=X_raw[sku].drop(['id','DayOfWeek','High_Var',"Luxury",'Customers','Sales'],axis=1)

In [6]:
for sku in list(df_dict.keys()):
    for obs in range(1,8):
        X_raw[sku]["Sales_T"+str(obs)]=df_dict[sku]['Sales'].shift(obs)
        

In [7]:
for sku in list(df_dict.keys()):
    X_raw[sku]["Mov_avg"]=df_dict[sku]['Sales'].rolling( window=7).mean().shift(1)

In [8]:
len(df)

9420

In [9]:
#Cut lagged vars NAs off top 
cut_lag=7;
for sku in list(df_dict.keys()):
    y[sku]=y[sku][cut_lag:]
    y[sku].reset_index(drop=True, inplace=True)
    
for sku in list(df_dict.keys()):
    X[sku]=X_raw[sku][cut_lag:]
    X[sku].reset_index(drop=True, inplace=True)

In [10]:
X[1].head()

Open  Promo  SchoolHoliday  Year  Month  Friday  Monday  Saturday  Sunday  \
0     1      1              1  2013      1       0       0         0       0   
1     1      1              1  2013      1       0       0         0       0   
2     1      1              1  2013      1       0       0         0       0   
3     1      1              1  2013      1       1       0         0       0   
4     1      0              0  2013      1       0       0         1       0   

   Thursday  Tuesday  Wednesday  Sales_T1  Sales_T2  Sales_T3  Sales_T4  \
0         0        1          0    7176.0       0.0    4997.0    4486.0   
1         0        0          1    5580.0    7176.0       0.0    4997.0   
2         1        0          0    5471.0    5580.0    7176.0       0.0   
3         0        0          0    4892.0    5471.0    5580.0    7176.0   
4         0        0          0    4881.0    4892.0    5471.0    5580.0   

   Sales_T5  Sales_T6  Sales_T7      Mov_avg  
0    4327.0    5530.0       0.0  3788.000000  
1    4486.0    4327.0    5530.0  4585.142857  
2    4997.0    4486.0    4327.0  4576.714286  
3       0.0    4997.0    4486.0  4657.428571  
4    7176.0       0.0    4997.0  4713.857143

In [11]:
std={}
for sku in list(df_dict.keys()):
    std[sku] = preprocessing.StandardScaler().fit(X[sku])
    X[sku] = std[sku].transform(X[sku])
std


{1: StandardScaler(copy=True, with_mean=True, with_std=True),
 2: StandardScaler(copy=True, with_mean=True, with_std=True),
 3: StandardScaler(copy=True, with_mean=True, with_std=True),
 4: StandardScaler(copy=True, with_mean=True, with_std=True),
 5: StandardScaler(copy=True, with_mean=True, with_std=True),
 6: StandardScaler(copy=True, with_mean=True, with_std=True),
 7: StandardScaler(copy=True, with_mean=True, with_std=True),
 8: StandardScaler(copy=True, with_mean=True, with_std=True),
 9: StandardScaler(copy=True, with_mean=True, with_std=True),
 10: StandardScaler(copy=True, with_mean=True, with_std=True)}

In [12]:
cv=5

RF=RandomForestRegressor( n_estimators=1000,max_depth=13,max_features=14);
# use a full grid over all parameters


rf_models=[];
for sku in list(df_dict.keys()):
    rf_models.append(cross_val_score(RF,X[sku],y[sku],cv=cv, scoring ='mean_absolute_error').mean().round(0) )
#
rf_models
cv

5

In [13]:

GB=ensemble.GradientBoostingRegressor(n_estimators= 200,max_depth= 4, max_features=16)#,learning_rate=0.01,loss='ls');
gb_models=[];
for sku in list(df_dict.keys()):
    gb_models.append(cross_val_score(GB,X[sku],y[sku],cv=cv, scoring ='mean_absolute_error').mean().round(0)  )
#    


In [14]:
XG=xgb.XGBRegressor(n_estimators= 100,max_depth=5,gamma=0)
xg_models=[]
for sku in list(df_dict.keys()):
    xg_models.append(cross_val_score(XG,X[sku],y[sku],cv=cv, scoring ='mean_absolute_error').mean().round(0)  )

In [15]:
def create_MLP():
    mlp=models.Sequential()
    mlp.add(Dense(20, input_dim=X[1].shape[1], activation='relu'))
    mlp.add(Dense(30, activation='relu'))
    #mlp.add(Dense(30, activation='relu'))
    mlp.add(Dense(10, activation='relu'))
    mlp.add(Dense(1))
    mlp.compile(loss='mae', optimizer='adam', metrics=['mae'])
    return mlp

MLP = KerasRegressor(build_fn=create_MLP,
                               epochs=700,
                               batch_size=25,
                               verbose=1)

In [16]:
mlp_models=[]
for sku in list(df_dict.keys()):
    mlp_models.append(cross_val_score(MLP,X[sku],y[sku],cv=cv).mean().round(0)  )

Epoch 1/700
748/748 [==============================] - 0s 467us/step - loss: 3891.9958 - mean_absolute_error: 3891.9958
Epoch 2/700
748/748 [==============================] - 0s 145us/step - loss: 3891.3248 - mean_absolute_error: 3891.3248
Epoch 3/700
748/748 [==============================] - 0s 112us/step - loss: 3889.7361 - mean_absolute_error: 3889.7361
Epoch 4/700
748/748 [==============================] - 0s 115us/step - loss: 3884.9582 - mean_absolute_error: 3884.9582
Epoch 5/700
748/748 [==============================] - 0s 111us/step - loss: 3872.0785 - mean_absolute_error: 3872.0785
Epoch 6/700
748/748 [==============================] - 0s 107us/step - loss: 3841.5224 - mean_absolute_error: 3841.5224
Epoch 7/700
748/748 [==============================] - 0s 115us/step - loss: 3779.8472 - mean_absolute_error: 3779.8472
Epoch 8/700
748/748 [==============================] - 0s 125us/step - loss: 3667.9328 - mean_absolute_error: 3667.9328
Epoch 9/700
748/748 [===================

748/748 [==============================] - 0s 98us/step - loss: 412.0451 - mean_absolute_error: 412.0451
Epoch 70/700
748/748 [==============================] - 0s 102us/step - loss: 410.9584 - mean_absolute_error: 410.9584
Epoch 71/700
748/748 [==============================] - 0s 110us/step - loss: 409.7825 - mean_absolute_error: 409.7825
Epoch 72/700
748/748 [==============================] - 0s 105us/step - loss: 408.9066 - mean_absolute_error: 408.9066
Epoch 73/700
748/748 [==============================] - 0s 101us/step - loss: 407.3018 - mean_absolute_error: 407.3018
Epoch 74/700
748/748 [==============================] - 0s 107us/step - loss: 406.1461 - mean_absolute_error: 406.1461
Epoch 75/700
748/748 [==============================] - 0s 103us/step - loss: 405.6935 - mean_absolute_error: 405.6935
Epoch 76/700
748/748 [==============================] - 0s 100us/step - loss: 406.0303 - mean_absolute_error: 406.0303
Epoch 77/700
748/748 [==============================] - 0s 107

748/748 [==============================] - 0s 103us/step - loss: 347.5818 - mean_absolute_error: 347.5818
Epoch 138/700
748/748 [==============================] - 0s 107us/step - loss: 348.3676 - mean_absolute_error: 348.3676
Epoch 139/700
748/748 [==============================] - 0s 106us/step - loss: 346.3884 - mean_absolute_error: 346.3884
Epoch 140/700
748/748 [==============================] - 0s 103us/step - loss: 347.9140 - mean_absolute_error: 347.9140
Epoch 141/700
748/748 [==============================] - 0s 109us/step - loss: 345.7094 - mean_absolute_error: 345.7094
Epoch 142/700
748/748 [==============================] - 0s 104us/step - loss: 345.6765 - mean_absolute_error: 345.6765
Epoch 143/700
748/748 [==============================] - 0s 104us/step - loss: 345.2127 - mean_absolute_error: 345.2127
Epoch 144/700
748/748 [==============================] - 0s 108us/step - loss: 344.5331 - mean_absolute_error: 344.5331
Epoch 145/700
748/748 [==============================]

748/748 [==============================] - 0s 106us/step - loss: 320.4290 - mean_absolute_error: 320.4290
Epoch 206/700
748/748 [==============================] - 0s 108us/step - loss: 319.3471 - mean_absolute_error: 319.3471
Epoch 207/700
748/748 [==============================] - 0s 108us/step - loss: 319.4922 - mean_absolute_error: 319.4922
Epoch 208/700
748/748 [==============================] - 0s 111us/step - loss: 318.5086 - mean_absolute_error: 318.5086
Epoch 209/700
748/748 [==============================] - 0s 108us/step - loss: 318.9735 - mean_absolute_error: 318.9735
Epoch 210/700
748/748 [==============================] - 0s 117us/step - loss: 317.7891 - mean_absolute_error: 317.7891
Epoch 211/700
748/748 [==============================] - 0s 109us/step - loss: 320.3370 - mean_absolute_error: 320.3370
Epoch 212/700
748/748 [==============================] - 0s 111us/step - loss: 318.1121 - mean_absolute_error: 318.1121
Epoch 213/700
748/748 [==============================]

Epoch 273/700
748/748 [==============================] - 0s 94us/step - loss: 297.0148 - mean_absolute_error: 297.0148
Epoch 274/700
748/748 [==============================] - 0s 101us/step - loss: 296.6312 - mean_absolute_error: 296.6312
Epoch 275/700
748/748 [==============================] - 0s 104us/step - loss: 297.8810 - mean_absolute_error: 297.8810
Epoch 276/700
748/748 [==============================] - 0s 112us/step - loss: 295.3429 - mean_absolute_error: 295.3429
Epoch 277/700
748/748 [==============================] - 0s 108us/step - loss: 296.2311 - mean_absolute_error: 296.2311
Epoch 278/700
748/748 [==============================] - 0s 104us/step - loss: 295.8308 - mean_absolute_error: 295.8308
Epoch 279/700
748/748 [==============================] - 0s 105us/step - loss: 295.8857 - mean_absolute_error: 295.8857
Epoch 280/700
748/748 [==============================] - 0s 106us/step - loss: 294.4840 - mean_absolute_error: 294.4840
Epoch 281/700
748/748 [==================

...

748/748 [==============================] - 0s 127us/step - loss: 296.6882 - mean_absolute_error: 296.6882
Epoch 427/700
748/748 [==============================] - 0s 124us/step - loss: 295.8659 - mean_absolute_error: 295.8659
Epoch 428/700
748/748 [==============================] - 0s 129us/step - loss: 297.4998 - mean_absolute_error: 297.4998
Epoch 429/700
748/748 [==============================] - 0s 136us/step - loss: 295.8670 - mean_absolute_error: 295.8670
Epoch 430/700
748/748 [==============================] - ETA: 0s - loss: 291.3705 - mean_absolute_error: 291.370 - 0s 132us/step - loss: 296.5213 - mean_absolute_error: 296.5213
Epoch 431/700
748/748 [==============================] - ETA: 0s - loss: 321.2546 - mean_absolute_error: 321.254 - 0s 129us/step - loss: 297.6957 - mean_absolute_error: 297.6957
Epoch 432/700
748/748 [==============================] - 0s 127us/step - loss: 297.1875 - mean_absolute_error: 297.1875
Epoch 433/700
748/748 [==============================] - 0

748/748 [==============================] - 0s 127us/step - loss: 295.7592 - mean_absolute_error: 295.7592
Epoch 494/700
748/748 [==============================] - 0s 132us/step - loss: 292.2242 - mean_absolute_error: 292.2242
Epoch 495/700
748/748 [==============================] - 0s 129us/step - loss: 292.2816 - mean_absolute_error: 292.2816
Epoch 496/700
748/748 [==============================] - 0s 124us/step - loss: 292.9346 - mean_absolute_error: 292.9346
Epoch 497/700
748/748 [==============================] - 0s 129us/step - loss: 293.6942 - mean_absolute_error: 293.6942
Epoch 498/700
748/748 [==============================] - 0s 128us/step - loss: 291.5243 - mean_absolute_error: 291.5243
Epoch 499/700
748/748 [==============================] - 0s 126us/step - loss: 291.6896 - mean_absolute_error: 291.6896
Epoch 500/700
748/748 [==============================] - 0s 139us/step - loss: 292.9937 - mean_absolute_error: 292.9937
Epoch 501/700
748/748 [==============================]

Epoch 560/700
748/748 [==============================] - 0s 133us/step - loss: 286.6860 - mean_absolute_error: 286.6860
Epoch 561/700
748/748 [==============================] - 0s 130us/step - loss: 288.1781 - mean_absolute_error: 288.1781
Epoch 562/700
748/748 [==============================] - 0s 128us/step - loss: 289.9790 - mean_absolute_error: 289.9790
Epoch 563/700
748/748 [==============================] - 0s 130us/step - loss: 287.7303 - mean_absolute_error: 287.7303
Epoch 564/700
748/748 [==============================] - 0s 128us/step - loss: 287.1869 - mean_absolute_error: 287.1869
Epoch 565/700
748/748 [==============================] - 0s 130us/step - loss: 286.8036 - mean_absolute_error: 286.8036
Epoch 566/700
748/748 [==============================] - 0s 139us/step - loss: 287.7187 - mean_absolute_error: 287.7187
Epoch 567/700
748/748 [==============================] - 0s 135us/step - loss: 287.0895 - mean_absolute_error: 287.0895
Epoch 568/700
748/748 [=================

748/748 [==============================] - 0s 127us/step - loss: 284.0253 - mean_absolute_error: 284.0253
Epoch 627/700
748/748 [==============================] - 0s 131us/step - loss: 284.5517 - mean_absolute_error: 284.5517
Epoch 628/700
748/748 [==============================] - 0s 138us/step - loss: 283.2936 - mean_absolute_error: 283.2936
Epoch 629/700
748/748 [==============================] - 0s 127us/step - loss: 284.8414 - mean_absolute_error: 284.8414
Epoch 630/700
748/748 [==============================] - 0s 127us/step - loss: 283.9843 - mean_absolute_error: 283.9843
Epoch 631/700
748/748 [==============================] - 0s 124us/step - loss: 285.7450 - mean_absolute_error: 285.7450
Epoch 632/700
748/748 [==============================] - 0s 129us/step - loss: 283.9113 - mean_absolute_error: 283.9113
Epoch 633/700
748/748 [==============================] - 0s 126us/step - loss: 283.3866 - mean_absolute_error: 283.3866
Epoch 634/700
748/748 [==============================]

748/748 [==============================] - 0s 128us/step - loss: 280.8525 - mean_absolute_error: 280.8525
Epoch 694/700
748/748 [==============================] - 0s 133us/step - loss: 281.2908 - mean_absolute_error: 281.2908
Epoch 695/700
748/748 [==============================] - 0s 135us/step - loss: 279.8093 - mean_absolute_error: 279.8093
Epoch 696/700
748/748 [==============================] - 0s 140us/step - loss: 282.1971 - mean_absolute_error: 282.1971
Epoch 697/700
748/748 [==============================] - 0s 121us/step - loss: 281.3626 - mean_absolute_error: 281.3626
Epoch 698/700
748/748 [==============================] - 0s 130us/step - loss: 281.4930 - mean_absolute_error: 281.4930
Epoch 699/700
748/748 [==============================] - 0s 124us/step - loss: 279.9676 - mean_absolute_error: 279.9676
Epoch 700/700
187/187 [==============================] - 1s 4ms/step


In [17]:
mae=-pd.DataFrame(np.column_stack((mlp_models,rf_models,gb_models,xg_models)) )
mae=mae.rename(columns = {0:'MLP',1:'RF',2:'GB',3:'XG'})
best=mae.idxmin(axis=1)
best.astype('category')
mae["Best"]=best
mae.index = mae.index + 1
mae.loc['mean'] = mae.mean()
mae['range']=mae.max(axis=1)-mae.min(axis=1)
mae

MLP     RF     GB     XG Best  range
1     370.0  339.0  366.0  350.0   RF   31.0
2     404.0  381.0  405.0  388.0   RF   24.0
3     607.0  557.0  609.0  588.0   RF   52.0
4     681.0  684.0  725.0  708.0  MLP   44.0
5     364.0  343.0  389.0  360.0   RF   46.0
6     408.0  385.0  397.0  405.0   RF   23.0
7     676.0  691.0  732.0  709.0  MLP   56.0
8     446.0  421.0  449.0  451.0   RF   30.0
9     537.0  537.0  550.0  537.0  MLP   13.0
10    395.0  363.0  385.0  375.0   RF   32.0
mean  488.8  470.1  500.7  487.1  NaN   30.6

In [18]:
#Need lots of rank and counts of how many times models came in 1st  vs 2nd.
def rank_model(df,rank):
    coln = 'Best' + str(rank) 
    sortID = np.argpartition(df[['MLP','RF','GB','XG']].values,rank,axis=1)[:,rank]
    df[coln] = df.columns[sortID]
    

In [19]:
rank_model(mae,0)
rank_model(mae,1)
mae

MLP     RF     GB     XG Best  range Best0 Best1
1     370.0  339.0  366.0  350.0   RF   31.0    RF    XG
2     404.0  381.0  405.0  388.0   RF   24.0    RF    XG
3     607.0  557.0  609.0  588.0   RF   52.0    RF    XG
4     681.0  684.0  725.0  708.0  MLP   44.0   MLP    RF
5     364.0  343.0  389.0  360.0   RF   46.0    RF    XG
6     408.0  385.0  397.0  405.0   RF   23.0    RF    GB
7     676.0  691.0  732.0  709.0  MLP   56.0   MLP    RF
8     446.0  421.0  449.0  451.0   RF   30.0    RF   MLP
9     537.0  537.0  550.0  537.0  MLP   13.0   MLP    RF
10    395.0  363.0  385.0  375.0   RF   32.0    RF    XG
mean  488.8  470.1  500.7  487.1  NaN   30.6    RF    XG

In [20]:
def RF_final(X, y):
    """
    Returns final predictions and final fitted version of RF
    """
    tree=RF
    tree.fit(X,y)
    pred=tree.predict(X)
    pred=pd.DataFrame(pred)
    pred.reset_index(drop=True, inplace=True)
    pred=pred.rename(columns = {0:'RF'})
    return (pred, tree)

def MLP_final(X,y):
    model = MLP
    model.fit(X,y)
    pred=model.predict(X)
    pred=pd.DataFrame(pred)
    pred.reset_index(drop=True, inplace=True)
    pred=pred.rename(columns = {0:'MLP'})
    return (pred, model)

def GB_final(X,y):
    model = GB
    model.fit(X,y)
    prediction=model.predict(X)
    pred=pd.DataFrame(prediction)
    pred.reset_index(drop=True, inplace=True)
    pred=pred.rename(columns = {0:'GB'})
    return (pred, model)

def XG_final(X,y):
    model=XG
    model.fit(X,y)
    prediction=model.predict(X)
    pred=pd.DataFrame(prediction)
    pred.reset_index(drop=True, inplace=True)
    pred=pred.rename(columns = {0:'XG'})
    return (pred, model)

In [21]:
#NOTE, because we are retraining models here, a bad initiatlization could lead to different results. 

def best_model(scores,X,y):
    d={}
    for sku in list(df_dict.keys()):
        
        if scores.loc[sku]["Best"]=="RF":     
            d[sku]=RF_final(X[sku],y[sku])
                    
        elif scores.loc[sku]["Best"]=="MLP":
            d[sku]=MLP_final(X[sku],y[sku])                 
            
        elif scores.loc[sku]["Best"]=="GB":
            d[sku]=GB_final(X[sku],y[sku])
            
        elif scores.loc[sku]["Best"]=="XG":
            d[sku]=XG_final(X[sku],y[sku])
      
    return d     

In [22]:
bm_dict=best_model(mae,X,y)
# bm_dict

Epoch 1/700
935/935 [==============================] - 2s 2ms/step - loss: 8029.3030 - mean_absolute_error: 8029.3030
Epoch 2/700
935/935 [==============================] - 0s 152us/step - loss: 8027.7135 - mean_absolute_error: 8027.7135
Epoch 3/700
935/935 [==============================] - 0s 144us/step - loss: 8023.0648 - mean_absolute_error: 8023.0648
Epoch 4/700
935/935 [==============================] - 0s 149us/step - loss: 8009.5514 - mean_absolute_error: 8009.5514
Epoch 5/700
935/935 [==============================] - 0s 162us/step - loss: 7975.6837 - mean_absolute_error: 7975.6837
Epoch 6/700
935/935 [==============================] - 0s 158us/step - loss: 7903.1111 - mean_absolute_error: 7903.1111
Epoch 7/700
935/935 [==============================] - 0s 147us/step - loss: 7765.8332 - mean_absolute_error: 7765.8332
Epoch 8/700
935/935 [==============================] - 0s 164us/step - loss: 7532.8627 - mean_absolute_error: 7532.8627
Epoch 9/700
935/935 [=====================

935/935 [==============================] - 0s 131us/step - loss: 776.0228 - mean_absolute_error: 776.0228
Epoch 69/700
935/935 [==============================] - 0s 131us/step - loss: 777.6623 - mean_absolute_error: 777.6623 0s - loss: 744.1922 - mean_absolute_error: 744.19
Epoch 70/700
935/935 [==============================] - 0s 131us/step - loss: 771.6073 - mean_absolute_error: 771.6073
Epoch 71/700
935/935 [==============================] - 0s 135us/step - loss: 771.0903 - mean_absolute_error: 771.0903
Epoch 72/700
935/935 [==============================] - 0s 136us/step - loss: 769.7958 - mean_absolute_error: 769.7958
Epoch 73/700
935/935 [==============================] - 0s 132us/step - loss: 768.5704 - mean_absolute_error: 768.5704
Epoch 74/700
935/935 [==============================] - 0s 129us/step - loss: 765.8684 - mean_absolute_error: 765.8684
Epoch 75/700
935/935 [==============================] - 0s 130us/step - loss: 764.5692 - mean_absolute_error: 764.5692
Epoch 76/70

935/935 [==============================] - 0s 128us/step - loss: 686.3186 - mean_absolute_error: 686.3186
Epoch 137/700
935/935 [==============================] - 0s 132us/step - loss: 689.3424 - mean_absolute_error: 689.3424
Epoch 138/700
935/935 [==============================] - 0s 130us/step - loss: 683.5951 - mean_absolute_error: 683.5951
Epoch 139/700
935/935 [==============================] - 0s 134us/step - loss: 686.4689 - mean_absolute_error: 686.4689
Epoch 140/700
935/935 [==============================] - 0s 133us/step - loss: 683.9941 - mean_absolute_error: 683.9941
Epoch 141/700
935/935 [==============================] - 0s 133us/step - loss: 683.3511 - mean_absolute_error: 683.3511
Epoch 142/700
935/935 [==============================] - 0s 127us/step - loss: 681.1398 - mean_absolute_error: 681.1398
Epoch 143/700
935/935 [==============================] - 0s 129us/step - loss: 681.2012 - mean_absolute_error: 681.2012
Epoch 144/700
935/935 [==============================]

935/935 [==============================] - 0s 126us/step - loss: 637.7928 - mean_absolute_error: 637.7928
Epoch 205/700
935/935 [==============================] - 0s 124us/step - loss: 636.9394 - mean_absolute_error: 636.9394
Epoch 206/700
935/935 [==============================] - 0s 131us/step - loss: 634.6948 - mean_absolute_error: 634.6948
Epoch 207/700
935/935 [==============================] - 0s 135us/step - loss: 637.4069 - mean_absolute_error: 637.4069
Epoch 208/700
935/935 [==============================] - 0s 132us/step - loss: 634.6975 - mean_absolute_error: 634.6975
Epoch 209/700
935/935 [==============================] - 0s 134us/step - loss: 634.2772 - mean_absolute_error: 634.2772
Epoch 210/700
935/935 [==============================] - 0s 133us/step - loss: 634.8624 - mean_absolute_error: 634.8624
Epoch 211/700
935/935 [==============================] - 0s 138us/step - loss: 635.2946 - mean_absolute_error: 635.2946
Epoch 212/700
935/935 [==============================]

935/935 [==============================] - 0s 138us/step - loss: 603.3041 - mean_absolute_error: 603.3041
Epoch 272/700
935/935 [==============================] - 0s 129us/step - loss: 601.3785 - mean_absolute_error: 601.3785
Epoch 273/700
935/935 [==============================] - 0s 131us/step - loss: 599.5412 - mean_absolute_error: 599.5412
Epoch 274/700
935/935 [==============================] - 0s 130us/step - loss: 598.9021 - mean_absolute_error: 598.9021
Epoch 275/700
935/935 [==============================] - 0s 133us/step - loss: 599.8495 - mean_absolute_error: 599.8495
Epoch 276/700
935/935 [==============================] - 0s 148us/step - loss: 599.1863 - mean_absolute_error: 599.1863 0s - loss: 598.4623 - mean_absolute_error: 598.46
Epoch 277/700
935/935 [==============================] - 0s 141us/step - loss: 599.1925 - mean_absolute_error: 599.1925
Epoch 278/700
935/935 [==============================] - 0s 132us/step - loss: 598.1352 - mean_absolute_error: 598.1352
Epoc

...

935/935 [==============================] - 0s 128us/step - loss: 388.1081 - mean_absolute_error: 388.1081
Epoch 417/700
935/935 [==============================] - 0s 133us/step - loss: 392.6852 - mean_absolute_error: 392.6852
Epoch 418/700
935/935 [==============================] - 0s 136us/step - loss: 387.9482 - mean_absolute_error: 387.9482
Epoch 419/700
935/935 [==============================] - 0s 132us/step - loss: 389.9336 - mean_absolute_error: 389.9336
Epoch 420/700
935/935 [==============================] - 0s 131us/step - loss: 388.4059 - mean_absolute_error: 388.4059
Epoch 421/700
935/935 [==============================] - 0s 126us/step - loss: 388.6224 - mean_absolute_error: 388.6224
Epoch 422/700
935/935 [==============================] - 0s 134us/step - loss: 389.0846 - mean_absolute_error: 389.0846
Epoch 423/700
935/935 [==============================] - 0s 141us/step - loss: 387.2617 - mean_absolute_error: 387.2617
Epoch 424/700
935/935 [==============================]

Epoch 484/700
935/935 [==============================] - 0s 130us/step - loss: 383.2292 - mean_absolute_error: 383.2292
Epoch 485/700
935/935 [==============================] - 0s 129us/step - loss: 380.3921 - mean_absolute_error: 380.3921
Epoch 486/700
935/935 [==============================] - 0s 136us/step - loss: 381.1427 - mean_absolute_error: 381.1427
Epoch 487/700
935/935 [==============================] - 0s 138us/step - loss: 383.5536 - mean_absolute_error: 383.5536
Epoch 488/700
935/935 [==============================] - 0s 129us/step - loss: 380.2335 - mean_absolute_error: 380.2335
Epoch 489/700
935/935 [==============================] - 0s 130us/step - loss: 381.3875 - mean_absolute_error: 381.3875
Epoch 490/700
935/935 [==============================] - 0s 128us/step - loss: 380.2008 - mean_absolute_error: 380.2008
Epoch 491/700
935/935 [==============================] - 0s 130us/step - loss: 380.5567 - mean_absolute_error: 380.5567
Epoch 492/700
935/935 [=================

935/935 [==============================] - 0s 128us/step - loss: 374.0098 - mean_absolute_error: 374.0098
Epoch 552/700
935/935 [==============================] - 0s 130us/step - loss: 375.5234 - mean_absolute_error: 375.5234
Epoch 553/700
935/935 [==============================] - 0s 131us/step - loss: 376.5006 - mean_absolute_error: 376.5006
Epoch 554/700
935/935 [==============================] - 0s 140us/step - loss: 373.8608 - mean_absolute_error: 373.8608
Epoch 555/700
935/935 [==============================] - 0s 130us/step - loss: 372.7603 - mean_absolute_error: 372.7603
Epoch 556/700
935/935 [==============================] - 0s 129us/step - loss: 373.5311 - mean_absolute_error: 373.5311
Epoch 557/700
935/935 [==============================] - 0s 130us/step - loss: 374.0726 - mean_absolute_error: 374.0726
Epoch 558/700
935/935 [==============================] - 0s 132us/step - loss: 373.2123 - mean_absolute_error: 373.2123
Epoch 559/700
935/935 [==============================]

935/935 [==============================] - 0s 145us/step - loss: 366.3100 - mean_absolute_error: 366.3100
Epoch 620/700
935/935 [==============================] - 0s 143us/step - loss: 364.2694 - mean_absolute_error: 364.2694
Epoch 621/700
935/935 [==============================] - 0s 146us/step - loss: 365.0785 - mean_absolute_error: 365.0785
Epoch 622/700
935/935 [==============================] - 0s 132us/step - loss: 364.6637 - mean_absolute_error: 364.6637
Epoch 623/700
935/935 [==============================] - 0s 134us/step - loss: 363.8381 - mean_absolute_error: 363.8381
Epoch 624/700
935/935 [==============================] - 0s 137us/step - loss: 365.7325 - mean_absolute_error: 365.7325
Epoch 625/700
935/935 [==============================] - 0s 137us/step - loss: 364.5219 - mean_absolute_error: 364.5219
Epoch 626/700
935/935 [==============================] - 0s 129us/step - loss: 363.8987 - mean_absolute_error: 363.8987
Epoch 627/700
935/935 [==============================]

935/935 [==============================] - 0s 129us/step - loss: 358.1199 - mean_absolute_error: 358.1199
Epoch 688/700
935/935 [==============================] - 0s 130us/step - loss: 358.3506 - mean_absolute_error: 358.3506
Epoch 689/700
935/935 [==============================] - 0s 133us/step - loss: 356.7981 - mean_absolute_error: 356.7981
Epoch 690/700
935/935 [==============================] - 0s 149us/step - loss: 357.1759 - mean_absolute_error: 357.1759
Epoch 691/700
935/935 [==============================] - 0s 131us/step - loss: 356.6091 - mean_absolute_error: 356.6091
Epoch 692/700
935/935 [==============================] - 0s 134us/step - loss: 356.7054 - mean_absolute_error: 356.7054
Epoch 693/700
935/935 [==============================] - 0s 132us/step - loss: 356.2583 - mean_absolute_error: 356.2583
Epoch 694/700
935/935 [==============================] - 0s 138us/step - loss: 354.9939 - mean_absolute_error: 354.9939
Epoch 695/700
935/935 [==============================]

In [23]:
#MAE of Best Model forecasting over all 935 days.  NN do very poorly here!
mae2=[]
for sku in list(df_dict.keys()):
    mae2.append( mean_absolute_error(y[sku], bm_dict[sku][0])   )
mae2=pd.DataFrame(mae2)
mae2.index = mae2.index + 1
mae2.round(1)
mae

MLP     RF     GB     XG Best  range Best0 Best1
1     370.0  339.0  366.0  350.0   RF   31.0    RF    XG
2     404.0  381.0  405.0  388.0   RF   24.0    RF    XG
3     607.0  557.0  609.0  588.0   RF   52.0    RF    XG
4     681.0  684.0  725.0  708.0  MLP   44.0   MLP    RF
5     364.0  343.0  389.0  360.0   RF   46.0    RF    XG
6     408.0  385.0  397.0  405.0   RF   23.0    RF    GB
7     676.0  691.0  732.0  709.0  MLP   56.0   MLP    RF
8     446.0  421.0  449.0  451.0   RF   30.0    RF   MLP
9     537.0  537.0  550.0  537.0  MLP   13.0   MLP    RF
10    395.0  363.0  385.0  375.0   RF   32.0    RF    XG
mean  488.8  470.1  500.7  487.1  NaN   30.6    RF    XG

In [24]:
sku_pred=pd.concat([ bm_dict[1][0],bm_dict[2][0],bm_dict[3][0],bm_dict[4][0],bm_dict[5][0],bm_dict[6][0],bm_dict[7][0],bm_dict[8][0],bm_dict[9][0],bm_dict[10][0],
],axis=1) 
sku_pred['Total'] = sku_pred.sum(axis=1)
sku_pred.columns = ['1','2','3','4','5','6','7','8','9','10','Total']
# sku_pred.to_csv('C:\\Users\\lengada1\\NCSU\\prediction_skus.csv')
sku_pred.to_csv('~/Downloads/NCSU-master-2/prediction_skus.csv')

#Each column in this dataframe is the result of 1 of the 4 models
sku_pred

1            2             3             4            5  \
0    5693.193925  6303.152272   9845.807535  10206.146484  5585.067958   
1    5539.595958  6555.860345   8411.639210   9118.957031  5824.338583   
2    5066.336187  5485.939943   7731.928681   9120.459961  4943.748700   
3    4861.325073  4855.833467   8811.058785   9824.867188  5083.340501   
4    4894.417490  2579.798593   4403.234392   9802.511719  1814.601078   
5       0.000000     0.000000      0.000000     -0.000415     0.000000   
6    4481.734005  3982.376276   4959.057241   7667.046387  3900.943029   
7    3991.253060  3931.732374   5114.052700   7145.960938  3744.720345   
8    3985.849512  4502.407539   5034.825950   6966.017090  3882.577859   
9    3940.036435  3621.608549   4793.865812   7111.237793  3568.472519   
10   4257.835932  3732.825022   5648.779211   7862.683105  4142.704268   
11   5071.419202  2442.788405   4043.308020   9452.623047  1740.935823   
12      0.000000     0.000000      0.000000     -0.000415     0.000000   
13   5688.485593  6525.428458   7298.995803  11558.269531  6688.294551   
14   5391.296616  5897.224629   8053.584502   9698.502930  5621.197018   
15   5419.990483  6098.431408   8244.381134   8914.590820  5833.915206   
16   5170.281643  5105.629560   7713.831549   9173.482422  4726.370882   
17   5368.695654  4691.972796   7551.550905   9231.973633  4970.776122   
18   5463.068434  2367.517173   4015.269666   9292.913086  1655.761885   
19      0.000000     0.000000      0.000000     -0.000415     0.000000   
20   4177.095675  3803.382927   5484.657638   7369.242676  3472.186931   
21   3835.155791  3693.718606   5197.609579   7074.893066  3546.645132   
22   4311.724652  4448.631449   5106.606630   7109.922363  3989.016014   
23   4607.849555  4111.031232   5499.725675   7485.521484  4181.763753   
24   5369.687974  4385.724477   6422.118387   9492.702148  4249.991662   
25   5787.877691  2903.038809   4792.584489  10541.937500  1787.431389   
26      0.000000     0.000000      0.000000     -0.000415     0.000000   
27   6932.883422  7020.373815  10925.417472  12874.765625  7158.474614   
28   6095.927355  6254.389478   9569.476554  11218.894531  5605.816722   
29   5986.525553  6599.758549   8794.797459  10160.733398  5655.510525   
..           ...          ...           ...           ...          ...   
905  5348.208602  6076.376935   7757.767164  11118.915039  5730.476935   
906  4905.314158  4849.685866   8075.081711  10658.730469  5090.969453   
907  4738.479190  4081.850481   4425.284637  10308.751953  2124.926481   
908     0.000000     0.000000      0.000000     -0.000415     0.000000   
909  4232.841532  4284.737788   6921.189396   8318.136719  4232.817253   
910  3815.253072  4161.885103   6346.959632   8354.769531  3950.291193   
911  3824.756825  5416.199265   6053.391261   8209.435547  4670.605984   
912  3798.743914  4093.433283   6216.791470   8672.015625  4466.336818   
913  3879.368990  4468.204644   6459.016821   9038.009766  4441.983138   
914  3870.449126  2791.512020   4111.169951  10464.303711  2064.508486   
915     0.000000     0.000000      0.000000     -0.000415     0.000000   
916  5260.657059  7240.537947   9563.680199  12843.463867  7587.269950   
917  5018.696120  6238.865893   8944.120388  11599.336914  6154.093711   
918  4856.605295  6592.050814   8473.066684  11010.261719  6071.968231   
919  4456.004934  5225.047137   7884.757067  11326.781250  5198.040697   
920  4671.376250  4660.835845   7103.963917  11020.164062  4758.230499   
921  4380.070413  3095.832132   4068.718592  10056.712891  2047.529659   
922     0.000000     0.000000      0.000000     -0.000415     0.000000   
923  4020.669476  4175.302887   5776.247655  10052.928711  4001.526487   
924  3742.651682  3998.851152   5717.849701   9145.597656  3731.709583   
925  3724.153775  5076.350548   5527.680708   8494.189453  3982.963289   
926  3694.788287  4162.106814   5648.429967   8915.905273  3737.749290   
927  3772.104656  3

In [25]:
# The rest of this notebook is just a reference and aid to allow collaborators to... 
# - save models
# - retrive and apply them without retraining. 

def save_model(model, filename):
    """
    Saves the model as a file. 
    - Keras models: saved as .json and .h5 files
    - scikit-learn models: saved as .pickle files
    """
    
    if type(model) is KerasRegressor:
        
        model_json = model.model.to_json()
        with open('{}.json'.format(filename), "w") as json_file:
            json_file.write(model_json)
        model.model.save_weights('{}.h5'.format(filename))        
    else:
        pickle_out = open('{}.pickle'.format(filename), "wb")
        pickle.dump(model, pickle_out)
        pickle_out.close()

    
# Save each SKU's best model to the local directory
for sku in list(df_dict.keys()):

    filename="SKU{}_best_model".format(sku)
    model = bm_dict[sku][1]

    save_model(model, filename)



In [26]:
# Load pickled models
# loaded_model = pickle.load(open('SKU1_best_model.pickle', 'rb'))
# print(type(loaded_model) is RandomForestRegressor)

def load_pickled_model(path_to_model):
    loaded_model = pickle.load(open(path_to_model, 'rb'))
    
    return loaded_model

def load_keras_model(path_to_json, path_to_weights_h5):
    
    # load json and create model
    json_file = open(path_to_json, 'r')
    loaded_model_json = json_file.read()
    json_file.close()
    loaded_model = model_from_json(loaded_model_json)

    # load weights into new model
    loaded_model.load_weights(path_to_weights_h5)
    
    # wrap Sequential obj as a KerasRegressor to allow scikit-learn compatibility
    wrapped_loaded_model = KerasRegressor(build_fn=create_MLP, epochs=400, batch_size=20, verbose=0)
    
    return wrapped_loaded_model

def load_model(filename):
    """
    Loads a given file as a model
    - .pickle files: loaded as scikit-learn models
    - .json and .h5 files: loaded together to create Keras models
    """
    
    loaded_model = None
    
    try:
        loaded_model = load_pickled_model("{}.pickle".format(filename))
        
    except FileNotFoundError:
        loaded_model = load_keras_model("{}.json".format(filename), "{}.h5".format(filename))
        
    return loaded_model
        
    
loaded_models={}
for i in range(1,11):
    model = load_model("SKU{}_best_model".format(i))
    loaded_models[i] = model

# loaded_models[9].compile(loss='mse', optimizer='adam', metrics=['mae','mse'])
# loaded_models[9].evaluate(X[9], y[9], verbose=0)


In [27]:
# Evaluate loaded model on test data
# loaded_model.compile(loss='mse', optimizer='adam', metrics=['mae','mse'])
# score = loaded_model.evaluate(Xs, y, verbose=0)
# print("%s: %.0f"%  (loaded_model.metrics_names[1], score[1]))
# print("%s: %.1f"%  (loaded_model.metrics_names[2], score[2]/10000000))

# Remember cv is cross validation, which is set to 2 earlier. Thus, X is divided into 2 subsets for train/test process
scores=[]
model_family=[]
for sku in range(1,11):
    
    # Identify the model family
    model = loaded_models[sku]
    if isinstance(model, RandomForestRegressor):
        model_family.append('RF')
    else:
        model_family.append('MLP')

    # Obtain the cross validation score
    score = -cross_val_score(model,X[sku],y[sku],cv=cv, scoring ='mean_absolute_error').mean().round(0)
    scores.append(score)        

loaded_model_scores = pd.DataFrame({
    'CV Score':scores,
    'Family':model_family
})
loaded_model_scores.index += 1

loaded_model_scores

CV Score Family
1      339.0     RF
2      380.0     RF
3      558.0     RF
4      685.0     RF
5      345.0     RF
6      386.0     RF
7      694.0     RF
8      421.0     RF
9      534.0    MLP
10     364.0     RF